In [121]:
# Outline
#

In [180]:
# Load packages
import pandas as pd
import os
import numpy as np
import collections
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn import tree

from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.model_selection import RandomizedSearchCV, train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import precision_score, recall_score, f1_score
from sklearn.pipeline import make_pipeline
from sklearn.tree import DecisionTreeClassifier

### Load Data

In [123]:
# Load data

dir_base = r"C:\Users\seedz\Desktop\Python\Option\analysis"
dir_train_data  = "all_comp.csv"

# Data Import and column naming
df_train = pd.read_csv(os.path.join(dir_base, dir_train_data))

df_train.head(10)

company_name                         website_standard  \
0                   Tenneco                 https://www.tenneco.com/   
1                       ADT                     https://www.adt.com/   
2               SAMSUNG SDS  http://www.samsungsds.com/en/index.html   
3                Gold's Gym                https://www.goldsgym.com/   
4    Advocate Aurora Health    https://www.advocateaurorahealth.org/   
5           Anytime Fitness          https://www.anytimefitness.com/   
6  Fairview Health Services                https://www.fairview.org/   
7          Menzies Aviation             https://menziesaviation.com/   
8                   ManTech                 https://www.mantech.com/   
9                 Firmenich               https://www.firmenich.com/   

                                         description     address_city  \
0  Tenneco is one of the world's leading designer...      Lake Forest   
1  ADT provides safe, smart and sustainable solut...       Boca Raton   
2  Our vision is driven by a fundamental desire t...  Ridgefield Park   
3  Gym has been the world’s trusted fitness autho...           Dallas   
4  Advocate Aurora Health and Atrium Health are n...        Milwaukee   
5  Anytime Fitness is the healthiest franchise op...         Hastings   
6  Fairview Health Services is Minnesota’s choice...      Minneapolis   
7  People. Passion. These have driven our team si...         Hounslow   
8  ManTech is more than a technology company. We ...          Herndon   
9  Firmenich is the largest privately-owned perfu...          New Ulm   

  address_admin1_name address_country_code                       industry  \
0            Illinois                   US    Motor Vehicle Manufacturing   
1             Florida                   US              Consumer Services   
2          New Jersey                   US  IT Services and IT Consulting   
3               Texas                   US  Wellness and Fitness Services   
4           Wisconsin                   US      Hospitals and Health Care   
5            Nebraska                   US  Wellness and Fitness Services   
6           Minnesota                   US      Hospitals and Health Care   
7             England                   GB          Airlines and Aviation   
8            Virginia                   US  IT Services and IT Consulting   
9           Minnesota                   US         Chemical Manufacturing   

   founded                                           keywords  employees_num  \
0     1930  Manufacturing of exhaust systems and component...        22855.0   
1     1874  Home Security || Business Security || Smart Ho...        22644.0   
2     1985  Enterprised Mobility || Advanced Analytics || ...        13146.0   
3     1965  Physical Fitness || Personal Training || Healt...        12904.0   
4     2018  Health Care || Hospitals || Outpatient Care ||...        12439.0   
5     2001  24 Hour Gyms || Fitness Centers || Health Club...        12237.0   
6     1905  Healthcare || Hospital || Primary Care Clinic ...        10958.0   
7     1833  Fuelling Services || air cargo || aviation || ...        10257.0   
8     1968  Cyber || Cybersecurity || Information Technolo...         9815.0   
9     1895  Fragrances || Flavors || Ingredients || Resear...         9165.0   

  company_size  location_counts  acquired     revenue  
0       10001+               30         1  7770700000  
1       10001+                1         1  7698960000  
2       10001+                4         1  4469640000  
3   5001-10000                2         1  4387360000  
4       10001+                2         1  4229260000  
5       51-200                1         1  4160580000  
6       10001+                1         1  3725720000  
7       10001+                3         1  3487380000  
8   5001-10000                1         1  3337100000  
9       10001+               38         1  3116100000

### Data checks

In [124]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8092 entries, 0 to 8091
Data columns (total 14 columns):
company_name            8092 non-null object
website_standard        8092 non-null object
description             8092 non-null object
address_city            8092 non-null object
address_admin1_name     8092 non-null object
address_country_code    8092 non-null object
industry                8092 non-null object
founded                 8092 non-null int64
keywords                8092 non-null object
employees_num           8092 non-null float64
company_size            8092 non-null object
location_counts         8092 non-null int64
acquired                8092 non-null int64
revenue                 8092 non-null int64
dtypes: float64(1), int64(4), object(9)
memory usage: 885.1+ KB


In [125]:
# check for nulls
df_train.isnull().sum()

company_name            0
website_standard        0
description             0
address_city            0
address_admin1_name     0
address_country_code    0
industry                0
founded                 0
keywords                0
employees_num           0
company_size            0
location_counts         0
acquired                0
revenue                 0
dtype: int64

In [126]:
# Inspect different values
print ('---Country---')
print (df_train['address_country_code'].value_counts())
print ('---Acquired (Target)---')
print (df_train['acquired'].value_counts())
print ('---Founded---')
print (df_train['founded'].value_counts())
print ('---Industry---')
print (df_train['industry'].value_counts())
print ('---City---')
print (df_train['address_city'].value_counts())


---Country---
US    5813
CA    1185
GB    1018
FR      26
IT      26
DE      20
CN       1
BR       1
CH       1
DK       1
Name: address_country_code, dtype: int64
---Acquired (Target)---
0    5000
1    3092
Name: acquired, dtype: int64
---Founded---
2014    263
2015    262
2013    258
2016    248
2012    240
2009    230
2010    228
2011    212
2001    205
2017    204
2008    194
2002    188
2006    186
2007    182
2004    182
2000    181
1999    176
2018    176
2005    173
2003    160
1998    142
1997    138
1996    130
1989    125
2019    121
1993    117
1984    112
1995    107
2020    104
1985    103
       ... 
1828      1
1848      1
1838      1
1856      1
1826      1
1818      1
1794      1
1854      1
1740      1
1866      1
1857      1
1861      1
1785      1
1867      1
1839      1
1899      1
1835      1
1819      1
1795      1
1561      1
1846      1
1879      1
1825      1
1829      1
1833      1
1837      1
1841      1
1845      1
1853      1
1640      1
Name: founded, L

In [127]:
df_train.describe(include='all')

company_name                     website_standard  \
count                          8092                                 8092   
unique                         7784                                 7791   
top     Executive Suites by Roseman  https://www.lindsaygoldbergllc.com/   
freq                              3                                    3   
mean                            NaN                                  NaN   
std                             NaN                                  NaN   
min                             NaN                                  NaN   
25%                             NaN                                  NaN   
50%                             NaN                                  NaN   
75%                             NaN                                  NaN   
max                             NaN                                  NaN   

                                              description address_city  \
count                                                8092         8092   
unique                                               7788         2063   
top     Science North is home to a world leading scien...     New York   
freq                                                    3          340   
mean                                                  NaN          NaN   
std                                                   NaN          NaN   
min                                                   NaN          NaN   
25%                                                   NaN          NaN   
50%                                                   NaN          NaN   
75%                                                   NaN          NaN   
max                                                   NaN          NaN   

       address_admin1_name address_country_code              industry  \
count                 8092                 8092                  8092   
unique                 108                   10                   161   
top             California                   US  Software Development   
freq                   975                 5813                   760   
mean                   NaN                  NaN                   NaN   
std                    NaN                  NaN                   NaN   
min                    NaN                  NaN                   NaN   
25%                    NaN                  NaN                   NaN   
50%                    NaN                  NaN                   NaN   
75%                    NaN                  NaN                   NaN   
max                    NaN                  NaN                   NaN   

            founded                                           keywords  \
count   8092.000000                                               8092   
unique          NaN                                               7782   
top             NaN  Private Equity || Venture Capital and Private ...   
freq            NaN                                                  6   
mean    1991.065126                                                NaN   
std       30.774144                                                NaN   
min     1561.000000                                                NaN   
25%     1983.000000                                                NaN   
50%     2001.000000                                                NaN   
75%     2011.000000                                                NaN   
max     2022.000000                                                NaN   

        employees_num company_size  location_counts     acquired       revenue  
count     8092.000000         8092      8092.000000  8092.000000  8.092000e+03  
unique            NaN            8              NaN          NaN           NaN  
top               NaN        11-50              NaN          NaN           NaN  
freq              NaN         2885              NaN          NaN           NaN  
mean       422.608131          NaN         2.80795

In [128]:
df_train.describe()

founded  employees_num  location_counts     acquired       revenue
count  8092.000000    8092.000000      8092.000000  8092.000000  8.092000e+03
mean   1991.065126     422.608131         2.807958     0.382106  1.267927e+08
std      30.774144    4098.277601         4.663641     0.485932  1.392152e+09
min    1561.000000       1.000000         1.000000     0.000000  1.050000e+05
25%    1983.000000      16.000000         1.000000     0.000000  2.048000e+06
50%    2001.000000      43.000000         1.000000     0.000000  5.504000e+06
75%    2011.000000     128.000000         3.000000     1.000000  2.496000e+07
max    2022.000000  238913.000000        95.000000     1.000000  8.123042e+10

### Dedupe

In [129]:
df_train = df_train.drop_duplicates()

In [130]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7832 entries, 0 to 8091
Data columns (total 14 columns):
company_name            7832 non-null object
website_standard        7832 non-null object
description             7832 non-null object
address_city            7832 non-null object
address_admin1_name     7832 non-null object
address_country_code    7832 non-null object
industry                7832 non-null object
founded                 7832 non-null int64
keywords                7832 non-null object
employees_num           7832 non-null float64
company_size            7832 non-null object
location_counts         7832 non-null int64
acquired                7832 non-null int64
revenue                 7832 non-null int64
dtypes: float64(1), int64(4), object(9)
memory usage: 917.8+ KB


In [131]:
pd.concat(g for _, g in df_train.groupby("company_name") if len(g) > 1)

company_name                      website_standard  \
334                             A-Gas                 https://www.agas.com/   
7279                            A-Gas                 https://www.agas.com/   
1285                       Abel Noser            https://www.abelnoser.com/   
7988                       Abel Noser            https://www.abelnoser.com/   
548          Altitude Energy Partners          https://www.altitude-ep.com/   
7804         Altitude Energy Partners          https://www.altitude-ep.com/   
1113              Ampco Pumps Company           https://www.ampcopumps.com/   
5278              Ampco Pumps Company           https://www.ampcopumps.com/   
529                           Avionos              https://www.avionos.com/   
3944                          Avionos              https://www.avionos.com/   
23                       Black Knight       https://www.blackknightinc.com/   
5035                     Black Knight       https://www.blackknightinc.com/   
576                    Blackhawk Bank        https://www.blackhawkbank.com/   
5752                   Blackhawk Bank        https://www.blackhawkbank.com/   
763                      CEP Forensic                http://cep-experts.ca/   
4116                     CEP Forensic                http://cep-experts.ca/   
50                            Calpine              https://www.calpine.com/   
4508                          Calpine              https://www.calpine.com/   
150                        CareOregon           https://www.careoregon.org/   
5652                       CareOregon           https://www.careoregon.org/   
1050                Codeplay Software             https://www.codeplay.com/   
7997                Codeplay Software             https://www.codeplay.com/   
936                          EdgeLink              http://www.edgelink.com/   
7183                         EdgeLink              http://www.edgelink.com/   
273                          Evernote             https://www.evernote.com/   
5302                         Evernote             https://www.evernote.com/   
768                            FINCAD               https://www.fincad.com/   
4802                           FINCAD                   https://fincad.com/   
109                         ForgeRock            https://www.forgerock.com/   
3265                        ForgeRock            https://www.forgerock.com/   
...                               ...                                   ...   
175                      Security 101          https://www.security101.com/   
5342                     Security 101          https://www.security101.com/   
1492         Seven Lakes Technologies          https://www.sevenlakes.com//   
6006         Seven Lakes Technologies          https://www.sevenlakes.com//   
1895               Stay-Lite Lighting             http://www.stay-lite.com/   
4169               Stay-Lite Lighting             http://www.stay-lite.com/   
912                           Synergi            http://www.synergillc.com/   
5095                          Synergi        https://www.teamsynergi.co.uk/   
276   Syntellis Performance Solutions            https://www.syntellis.com/   
5781  Syntellis Performance Solutions            https://www.syntellis.com/   
373                      TigerConnect             https://tigerconnect.com/   
3333                     TigerConnect             https://tigerconnect.com/   
1903                 Total Air Supply           https://totalairsupply.com/   
5267                 Total Air Supply           https://totalairsupply.com/   
2167             Tour Experience Golf                       https://txg.ca/   
7155             Tour Experience Golf                       https://txg.ca/   
10                   Univar Solutions      https://www.univarsolutions.com/   
4716                 Univar Solutions      https://www.univarsolutions.com/   
67                        UserTesting          https://www.usertesting.com/

### Exploring keywords data

In [132]:
arr = []
for ii in df_train['keywords']:
    s = ii.split(" || ")
    arr += s
    #print (s)

counter = collections.Counter(arr)
counter_sorted = sorted(counter.items(), key=lambda x:x[1], reverse=True)
for i,x in enumerate(counter_sorted):
    print (i,x)

0 ('Software Development', 784)
1 ('IT Services and IT Consulting', 718)
2 ('Financial Services', 415)
3 ('Advertising Services', 403)
4 ('Construction', 330)
5 ('Hospitals and Health Care', 239)
6 ('Non-profit Organizations', 212)
7 ('Retail', 189)
8 ('Real Estate', 178)
9 ('Manufacturing', 178)
10 ('Insurance', 162)
11 ('Marketing', 159)
12 ('Banking', 137)
13 ('Technology', 136)
14 ('Education', 133)
15 ('Business Consulting and Services', 127)
16 ('Telecommunications', 121)
17 ('Truck Transportation', 121)
18 ('Artificial Intelligence', 117)
19 ('Project Management', 114)
20 ('Wellness and Fitness Services', 112)
21 ('SaaS', 111)
22 ('Digital Marketing', 111)
23 ('Healthcare', 109)
24 ('Biotechnology Research', 109)
25 ('Staffing and Recruiting', 109)
26 ('Technology, Information and Internet', 109)
27 ('Machine Learning', 106)
28 ('Social Media', 105)
29 ('Design', 104)
30 ('Consulting', 102)
31 ('Oil and Gas', 102)
32 ('Motor Vehicle Manufacturing', 100)
33 ('Hospitality', 96)
34

816 ('Optimization', 8)
817 ('Quality', 8)
818 ('Wound Care', 8)
819 ('human resources', 8)
820 ('Disability Insurance', 8)
821 ('Data Centers', 8)
822 ('RFID', 8)
823 ('e-learning', 8)
824 ('Integrations', 8)
825 ('Video Conferencing', 8)
826 ('User Research', 8)
827 ('Process Engineering', 8)
828 ('recruitment', 8)
829 ('RPO', 8)
830 ('Drupal', 8)
831 ('.NET', 8)
832 ('Advisory', 8)
833 ('Physical Therapy', 8)
834 ('Productivity', 8)
835 ('Revenue Management', 8)
836 ('Plastic Surgery', 8)
837 ('Search Engine Optimization (SEO)', 8)
838 ('UX Design', 8)
839 ('Smart Cities', 8)
840 ('Google Cloud', 8)
841 ('Incident Management', 8)
842 ('Performance Marketing', 8)
843 ('science', 8)
844 ('Business Process Outsourcing', 8)
845 ('Telecom', 8)
846 ('Games', 8)
847 ('Market Intelligence', 8)
848 ('email marketing', 8)
849 ('New Homes', 8)
850 ('Financial Management', 8)
851 ('IT Staffing', 8)
852 ('management', 8)
853 ('EV Charging', 8)
854 ('Dining', 8)
855 ('Dynamics 365', 8)
856 ('ware

1565 ('NetSuite', 5)
1566 ('Broadcasting', 5)
1567 ('Administration', 5)
1568 ('Gamification', 5)
1569 ('telemedicine', 5)
1570 ('technical support', 5)
1571 ('Customization', 5)
1572 ('Financial Reporting', 5)
1573 ('Recruitment Marketing', 5)
1574 ('Loss Prevention', 5)
1575 ('Information Technology Consulting', 5)
1576 ('Safety Training', 5)
1577 ('Prototypes', 5)
1578 ('Restoration', 5)
1579 ('Connected Devices', 5)
1580 ('Laser Cutting', 5)
1581 ('Health and Wellness', 5)
1582 ('Agile Transformation', 5)
1583 ('AML', 5)
1584 ('Supply Chain Solutions', 5)
1585 ('Preschool', 5)
1586 ('Instructional Design', 5)
1587 ('Vulnerability Assessments', 5)
1588 ('Lean', 5)
1589 ('Benchmarking', 5)
1590 ('Certificates of Deposit', 5)
1591 ('PEO', 5)
1592 ('Pumps', 5)
1593 ('CMMC', 5)
1594 ('Process Improvement', 5)
1595 ('Repair', 5)
1596 ('Retail Banking', 5)
1597 ('veterans', 5)
1598 ('mHealth', 5)
1599 ('Internal Communications', 5)
1600 ('Mutual Funds', 5)
1601 ('Wayfinding', 5)
1602 ('in

2315 ('Wastewater treatment', 3)
2316 ("Women's health", 3)
2317 ('Minimally Invasive Surgery', 3)
2318 ('Pain', 3)
2319 ('Market access', 3)
2320 ('Robotic Process Automation (RPA)', 3)
2321 ('Electronic Data Capture', 3)
2322 ('email security', 3)
2323 ('Industry', 3)
2324 ('Health & Beauty', 3)
2325 ('Finance and Accounting', 3)
2326 ('Administrative', 3)
2327 ('Billing', 3)
2328 ('Sales Engagement', 3)
2329 ('Customer Acquisition', 3)
2330 ('Casino', 3)
2331 ('Nightclub', 3)
2332 ('Occupational Health', 3)
2333 ('Digitalisation', 3)
2334 ('Water Heaters', 3)
2335 ('marketing insights', 3)
2336 ('customer journey mapping', 3)
2337 ('Consultants', 3)
2338 ('Steam', 3)
2339 ('IT Consulting Services', 3)
2340 ('Cyber Incident Response', 3)
2341 ('Skylights', 3)
2342 ('Flatbed', 3)
2343 ('Dedicated', 3)
2344 ('Client Gifts', 3)
2345 ('Employee Recognition', 3)
2346 ('Laundry', 3)
2347 ('MFA', 3)
2348 ('Menswear', 3)
2349 ('mobile banking', 3)
2350 ('Telemarketing', 3)
2351 ('Live Chat',

3065 ('Branded Merchandise', 3)
3066 ('Cabinets', 3)
3067 ('fittings', 3)
3068 ('Access Management', 3)
3069 ('Infographics', 3)
3070 ('Brochures', 3)
3071 ('Disability', 3)
3072 ('online sales', 3)
3073 ('Corporate Social Responsibility', 3)
3074 ('Teachers', 3)
3075 ('Educational Technology', 3)
3076 ('Shearing', 3)
3077 ('Permanent Recruitment', 3)
3078 ('Office furniture', 3)
3079 ('Enterprise Technology', 3)
3080 ('Switches', 3)
3081 ('Dental Care', 3)
3082 ('ELK', 3)
3083 ('Microbiology', 3)
3084 ('esports', 3)
3085 ('Zero Trust', 3)
3086 ('diversity', 3)
3087 ('Injury Prevention', 3)
3088 ('Government Services', 3)
3089 ('User Testing', 3)
3090 ('Workplace Investigations', 3)
3091 ('Voice Solutions', 3)
3092 ('Business development', 3)
3093 ('iGaming', 3)
3094 ('Custom software development', 3)
3095 ('herbs', 3)
3096 ('PPM', 3)
3097 ('Predictive Maintenance', 3)
3098 ('ISO 13485', 3)
3099 ('smart buildings', 3)
3100 ('Preventive Maintenance', 3)
3101 ('HubSpot', 3)
3102 ('psycho

...

42053 ('arts and culture', 1)
42054 ('SEO/SEM/PPC', 1)
42055 ('Contentwriting', 1)
42056 ('Charter Services', 1)
42057 ('Hand Carries', 1)
42058 ('Tradeshow Services', 1)
42059 ('Trade Compliance - ITAR/EAR', 1)
42060 ('Foreign-to-Foreign', 1)
42061 ('Films', 1)
42062 ('Music Videos', 1)
42063 ('Documentaries & Special event video coverage', 1)
42064 ('Corporate Videos and Company Portfolios', 1)
42065 ('brand design and brand communication', 1)
42066 ('motion design', 1)
42067 ('Zoo', 1)
42068 ('Sustainable business models', 1)
42069 ('Online learning', 1)
42070 ('Behaviour change campaigns', 1)
42071 ('Impact data management and analysis', 1)
42072 ('Public/Private Partnership', 1)
42073 ('Order Verification', 1)
42074 ('Supply Chain level sensor network', 1)
42075 ('APIs allow sharing of data', 1)
42076 ('Integration Application integrates with partner Marketplaces,', 1)
42077 ('Ag and Consumer Loans', 1)
42078 ('Mobile banking & On-Line Banking', 1)
42079 ('before school', 1)
42080

42969 ('chemicals', 1)
42970 ('paint', 1)
42971 ('hooks', 1)
42972 ('tools', 1)
42973 ('User Experience Consulting & Design', 1)
42974 ('Canadian', 1)
42975 ('Growth equity and venture capital investing focused on growth industries including technology', 1)
42976 ('healthcare & life sciences', 1)
42977 ('business & financial services', 1)
42978 ('education and industrial.', 1)
42979 ('Medication Assistance', 1)
42980 ('Co-Occurring', 1)
42981 ('Motivational Interviewing', 1)
42982 ('Long-term Residential', 1)
42983 ('Spiritual Care', 1)
42984 ('Sober Living Houses', 1)
42985 ('Recreation Therapy', 1)
42986 ('Gender Specific', 1)
42987 ('withdrawal management', 1)
42988 ('In-Home Care', 1)
42989 ('Nursing Home Transitioning', 1)
42990 ('Independent Living Skills Training', 1)
42991 ('Consumer-Directed Services', 1)
42992 ('Youth Transitioning', 1)
42993 ('Disability Awareness Program', 1)
42994 ('Macro and policy surprises', 1)
42995 ('Market cycles', 1)
42996 ('Investor positioning', 1

43802 ('Sick Sensors', 1)
43803 ('Sick Bar Code', 1)
43804 ('Baumer', 1)
43805 ('Teco', 1)
43806 ('Turck', 1)
43807 ('Schmersal', 1)
43808 ('SMC', 1)
43809 ('Industrial Products', 1)
43810 ('Mechanical Products', 1)
43811 ('Waterworks Products', 1)
43812 ('Mining Products', 1)
43813 ('Oil and Gas Products', 1)
43814 ('Day Care', 1)
43815 ('Summer camp', 1)
43816 ('Afterschool care', 1)
43817 ('GCSEs', 1)
43818 ('Coeducation', 1)
43819 ('Alumni', 1)
43820 ('Cricket', 1)
43821 ('Netball', 1)
43822 ('Chess', 1)
43823 ('Futsal', 1)
43824 ('Managed Cloud Solutions', 1)
43825 ('Dedicated Hardware', 1)
43826 ('Managed Colocation', 1)
43827 ('Private Cloud Hosting', 1)
43828 ('Metro Wireless', 1)
43829 ('Tableu', 1)
43830 ('Salesforce Sales & Market Cloud', 1)
43831 ('Salesforce Education & Heath Cloud', 1)
43832 ('ServiceNow ITSM', 1)
43833 ('ServiceNow Enterprise Management App Eco System', 1)
43834 ('ServiceNow ITBM', 1)
43835 ('ServiceNow SecOps & GRC', 1)
43836 ('ServiceNow Asset Manageme

44552 ('Parking Signage', 1)
44553 ('Wall Graphics', 1)
44554 ('Branded Signage', 1)
44555 ('Architectural Graphics', 1)
44556 ('3D Signage', 1)
44557 ('Private Equity Buyouts', 1)
44558 ('Majority Recapitalizations', 1)
44559 ('Service Companies', 1)
44560 ('Companies with $10M-$100M Revenue and $3M-$10M EBITDA', 1)
44561 ('Technicial', 1)
44562 ('DRCM', 1)
44563 ('Call Center Technology', 1)
44564 ('voice self-service', 1)
44565 ('Call Routing', 1)
44566 ('Azure AD', 1)
44567 ('Mobile Management', 1)
44568 ('Id & Access Management', 1)
44569 ('System Center 2012', 1)
44570 ('MS Exchange', 1)
44571 ('Desktop Deployment', 1)
44572 ('HyperV', 1)
44573 ('SCOM & SCCM', 1)
44574 ('AD Managed Services', 1)
44575 ('Skype for Business', 1)
44576 ('AD Divestitures and Mergers', 1)
44577 ('ADFS', 1)
44578 ('Windows Servers', 1)
44579 ('teams', 1)
44580 ('behavioral analytics', 1)
44581 ('healthcare analytics', 1)
44582 ('challenge-based learning', 1)
44583 ('Trophies', 1)
44584 ('Medals', 1)
44

45302 ('Rheology', 1)
45303 ('Tailings', 1)
45304 ('Fluid Dynamics', 1)
45305 ('Physical Modelling', 1)
45306 ('Mixing', 1)
45307 ('Pet Adoption', 1)
45308 ('Lost Pet Reunion & Intake', 1)
45309 ('Sales Force Automation', 1)
45310 ('Direct Store Delivery', 1)
45311 ('Real Estate Development and Management', 1)
45312 ('Outlet Centers', 1)
45313 ('Regional Centers', 1)
45314 ('Airport Retail', 1)
45315 ('Mixed-Use and Office Developments', 1)
45316 ('Marinas', 1)
45317 ('Golf Courses', 1)
45318 ('Planned Communities', 1)
45319 ('Street-front Retail', 1)
45320 ('#Retail Leasing', 1)
45321 ('expert witness consulting', 1)
45322 ('litigation strategy', 1)
45323 ('expert reports', 1)
45324 ('Arts and Humanities', 1)
45325 ('Theatre Film TV', 1)
45326 ('Management Law', 1)
45327 ('Sociology/social policy', 1)
45328 ('Educational studies', 1)
45329 ('Executive Education', 1)
45330 ('Customized Professional Skincare Products and Treatments', 1)
45331 ('business analysis', 1)
45332 ('high-tech a


### Generate new features

In [133]:
def website_sfx(row):
    if '.ac.uk/' in row['website_standard']:
        return 'ac_uk'
    if '.ai/' in row['website_standard']:
        return 'ai'
    if '.edu/' in row['website_standard']:
        return 'edu'
    if '.io/' in row['website_standard']:
        return 'io'
    if '.net/' in row['website_standard']:
        return 'net'
    if '.org.uk/' in row['website_standard']:
        return 'org'
    if '.org/' in row['website_standard']:
        return 'org'
    if '.tv/' in row['website_standard']:
        return 'tv'
    return 'other'

In [134]:
def founded_era(row):
	if row['founded'] < 1960:
		return 'A: pre-1960'
	if row['founded'] in range(1960,1970):
		return 'B: 1960s'
	if row['founded'] in range(1970,1980):
		return 'C: 1970s'
	if row['founded'] in range(1980,1990):
		return 'D: 1980s'
	if row['founded'] in range(1990,2000):
		return 'E: 1990s'
	if row['founded'] in range(2000,2010):
		return 'F: 2000s'
	if row['founded'] in range(2010,2020):
		return 'G: 2010s'
	if row['founded'] in range(2020,2030):
		return 'H: 2020s'
	return 'I: unk'

In [135]:
def city_top(row):
    cities = ['New York' ,'London','Toronto' ,'San Francisco' ,'Greater London' ,'Chicago' ,'Vancouver' ,'Austin' ,'Calgary' ,'Houston' ,'Los Angeles' ,'Atlanta' ,'Boston','San Diego' ,'Washington' ,'Dallas' ,'Montréal' ,'Denver','Seattle' ,'Minneapolis']
    if row['address_city'] in cities:
        return row['address_city']
    return 'Other'

In [136]:
def industry_top(row):
    industries = ['Software Development','IT Services and IT Consulting','Advertising Services','Financial Services','Construction','Hospitals and Health Care','Non-profit Organizations','Real Estate','Insurance','Business Consulting and Services','Retail','Truck Transportation','Banking','Wellness and Fitness Services','Biotechnology Research','Staffing and Recruiting','Technology, Information and Internet','Telecommunications','Motor Vehicle Manufacturing','Oil and Gas']
    if row['industry'] in industries:
        return row['industry']
    return 'Other'

In [137]:
def software(row):
    a = ['Software Development', 'SaaS', 'IT Services and IT Consulting']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def finance(row):
    a = ['Financial Services', 'Banking']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def advert(row):
    a = ['Advertising Services']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def constr(row):
    a = ['Construction']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def health(row):
    a = ['Hospitals and Health Care']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def NPO(row):
    a = ['Non-profit Organizations']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def retail(row):
    a = ['Retail']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def realest(row):
    a = ['Real Estate']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def manuf(row):
    a = ['Manufacturing']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def insurance(row):
    a = ['Insurance']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def market(row):
    a = ['Marketing', 'Digital Marketing']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def tech(row):
    a = ['Technology', 'Technology, Information and Internet']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def edu(row):
    a = ['Education']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def consult(row):
    a = ['Business Consulting and Services']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def telco(row):
    a = ['Telecommunications']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def AIML(row):
    a = ['Artificial Intelligence', 'Machine Learning']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def projman(row):
    a = ['Project Management']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def health(row):
    a = ['Wellness and Fitness Services', 'Healthcare']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0

def biotech(row):
    a = ['Biotechnology Research']
    if any((True for x in a if x in row['keywords'])):
        return 1
    return 0


In [138]:
def location_grp(row):
	if row['location_counts'] <= 20:
		return str(row['location_counts'])
	return '20+'

In [139]:
df_train['website_sfx'] = df_train.apply(website_sfx, axis=1)
df_train['founded_era'] = df_train.apply(founded_era, axis=1)
df_train['city_top'] = df_train.apply(city_top, axis=1)
df_train['industry_top'] = df_train.apply(industry_top, axis=1)
df_train['location_grp'] = df_train.apply(location_grp, axis=1)


In [140]:
df_train['finance']   = df_train.apply(finance, axis=1) 
df_train['advert']    = df_train.apply(advert, axis=1) 
df_train['constr']    = df_train.apply(constr, axis=1) 
df_train['health']    = df_train.apply(health, axis=1) 
df_train['NPO'] 	   = df_train.apply(NPO, axis=1) 
df_train['retail']    = df_train.apply(retail, axis=1) 
df_train['realest']   = df_train.apply(realest, axis=1) 
df_train['manuf'] 	   = df_train.apply(manuf, axis=1) 
df_train['insurance'] = df_train.apply(insurance, axis=1) 
df_train['market']    = df_train.apply(market, axis=1) 
df_train['tech'] 	   = df_train.apply(tech, axis=1) 
df_train['edu'] 	   = df_train.apply(edu, axis=1) 
df_train['consult']   = df_train.apply(consult, axis=1) 
df_train['telco'] 	   = df_train.apply(telco, axis=1) 
df_train['AIML'] 	   = df_train.apply(AIML, axis=1) 
df_train['projman']   = df_train.apply(projman, axis=1) 
df_train['health']    = df_train.apply(health, axis=1) 
df_train['biotech']   = df_train.apply(biotech, axis=1) 


In [143]:
df_train['unique_key'] = df_train['company_name']+'_'+df_train['founded'].astype(str)+'_'+df_train['address_country_code']

In [144]:
df_train

company_name  \
0                                   Tenneco   
1                                       ADT   
2                               SAMSUNG SDS   
3                                Gold's Gym   
4                    Advocate Aurora Health   
5                           Anytime Fitness   
6                  Fairview Health Services   
7                          Menzies Aviation   
8                                   ManTech   
9                                 Firmenich   
10                         Univar Solutions   
11                                 Diversey   
12                               CDK Global   
13                                 Amedisys   
14                              Micro Focus   
15                                   Vivint   
16                                  Zendesk   
17                                Qualtrics   
18                                 Worldpay   
19                            Mattress Firm   
20                 Ness Digital Engineering   
21                                 Entegris   
22                                LHC Group   
23                             Black Knight   
24                            ACI Worldwide   
25                                   NEORIS   
26                       Future Electronics   
27                         The Fresh Market   
28                 TravelCenters of America   
29                    Teachers Pay Teachers   
...                                     ...   
8062                        6teen30 Digital   
8063  Breckenridge Outdoor Education Center   
8064                                 InVcap   
8065                      Regent Properties   
8066                          Bio-Solutions   
8067                           Bonney Forge   
8068                          JPI Solutions   
8069                           Peopledesign   
8070               Bio Behavioral Institute   
8071                            Healthfirst   
8072                          Emerald Ocean   
8073                               Merchbro   
8074    JACKSONVILLE FIREMEN'S CREDIT UNION   
8075                 Premier Coil Solutions   
8076                          One Week Bath   
8077                    The Persimmon Group   
8078                                  HeroX   
8079                 Northern States Metals   
8080                         Lloyd Staffing   
8081     Greater Reston Chamber of Commerce   
8082               Wayfarer Insurance Group   
8083           EMERGE Community Development   
8084                              CoreStack   
8085           WEST MERCIA FORK LIFT TRUCKS   
8086                               CIPIO.ai   
8087                    Hawthorn Foundation   
8088                       Greater Than One   
8089              DeWind One-Pass Trenching   
8090                                MedRisk   
8091                                   iCEV   

                             website_standard  \
0                    https://www.tenneco.com/   
1                        https://www.adt.com/   
2     http://www.samsungsds.com/en/index.html   
3                   https://www.goldsgym.com/   
4       https://www.advocateaurorahealth.org/   
5             https://www.anytimefitness.com/   
6                   https://www.fairview.org/   
7                https://menziesaviation.com/   
8                    https://www.mantech.com/   
9                  https://www.firmenich.com/   
10           https://www.univarsolutions.com/   
11                  https://www.diversey.com/   
12                  http://www.cdkglobal.com/   
13                  https://www.amedisys.com/   
14       http://www.microfocus.com/en-us/home   
15                    https://www.vivint.com/   
16                   https://www.zendesk.com/   
17                 https://www.qualtrics.com/   
18                  https://www.worldpay.com/   
19              https://www.mattressfirm.com/   
20                      https://www.ness.com/   
21                  https://www.entegr

In [145]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7832 entries, 0 to 8091
Data columns (total 37 columns):
company_name            7832 non-null object
website_standard        7832 non-null object
description             7832 non-null object
address_city            7832 non-null object
address_admin1_name     7832 non-null object
address_country_code    7832 non-null object
industry                7832 non-null object
founded                 7832 non-null int64
keywords                7832 non-null object
employees_num           7832 non-null float64
company_size            7832 non-null object
location_counts         7832 non-null int64
acquired                7832 non-null int64
revenue                 7832 non-null int64
website_sfx             7832 non-null object
founded_era             7832 non-null object
city_top                7832 non-null object
industry_top            7832 non-null object
location_grp            7832 non-null object
finance                 7832 non-null int

In [148]:
# drop unnecessary cols

df_train=df_train.drop(columns=['company_name' ,'website_standard' ,'description' ,'address_city','address_admin1_name' ,'industry'  ,'founded','keywords'])


In [150]:
df_train

address_country_code  employees_num company_size  location_counts  \
0                      US        22855.0       10001+               30   
1                      US        22644.0       10001+                1   
2                      US        13146.0       10001+                4   
3                      US        12904.0   5001-10000                2   
4                      US        12439.0       10001+                2   
5                      US        12237.0       51-200                1   
6                      US        10958.0       10001+                1   
7                      GB        10257.0       10001+                3   
8                      US         9815.0   5001-10000                1   
9                      US         9165.0       10001+               38   
10                     US         8587.0   5001-10000               11   
11                     US         8580.0   5001-10000                2   
12                     US         8484.0   5001-10000                2   
13                     US         8025.0       10001+                1   
14                     GB         7579.0       10001+                4   
15                     US         6744.0       10001+                3   
16                     US         6376.0    1001-5000                8   
17                     US         6059.0   5001-10000               18   
18                     US         5954.0   5001-10000                2   
19                     US         5905.0   5001-10000                1   
20                     US         5459.0    1001-5000                1   
21                     US         5086.0   5001-10000               53   
22                     US         5085.0       10001+                1   
23                     US         4838.0   5001-10000                2   
24                     US         4700.0    1001-5000               35   
25                     US         4698.0    1001-5000               20   
26                     CA         4405.0    1001-5000                3   
27                     US         4398.0       10001+                1   
28                     US         4047.0       10001+                1   
29                     US         3872.0       51-200                2   
...                   ...            ...          ...              ...   
8062                   US           10.0        11-50                1   
8063                   US           59.0        11-50                4   
8064                   CA            4.0        11-50                2   
8065                   US          107.0       51-200                1   
8066                   US            1.0         1-10                1   
8067                   US          136.0     501-1000                3   
8068                   CA           19.0        11-50                3   
8069                   US           11.0        11-50                1   
8070                   US           11.0        11-50                1   
8071                   US         4123.0    1001-5000                3   
8072                   CA            1.0        11-50                3   
8073                   US            7.0         1-10                2   
8074                   US            9.0         1-10                2   
8075                   US           48.0       51-200                1   
8076                   US           21.0        11-50                1   
8077                   US           44.0        11-50                1   
8078                   CA           35.0        11-50                3   
8079                   US           46.0       51-200                1   
8080                   US          204.0       51-200                4   
8081                   US           18.0         1-10                1   
8082                   CA           19.0        11-50                1   
8083                   US           75.0       51-200                4   
8084     

In [149]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7832 entries, 0 to 8091
Data columns (total 29 columns):
address_country_code    7832 non-null object
employees_num           7832 non-null float64
company_size            7832 non-null object
location_counts         7832 non-null int64
acquired                7832 non-null int64
revenue                 7832 non-null int64
website_sfx             7832 non-null object
founded_era             7832 non-null object
city_top                7832 non-null object
industry_top            7832 non-null object
location_grp            7832 non-null object
finance                 7832 non-null int64
advert                  7832 non-null int64
constr                  7832 non-null int64
health                  7832 non-null int64
NPO                     7832 non-null int64
retail                  7832 non-null int64
realest                 7832 non-null int64
manuf                   7832 non-null int64
insurance               7832 non-null int64
mark

In [151]:
print (df_train['address_country_code'].value_counts())  
print (df_train['company_size'].value_counts())  
print (df_train['location_counts'].value_counts())  
print (df_train['acquired'].value_counts())    
print (df_train['website_sfx'].value_counts())  
print (df_train['founded_era'].value_counts())  
print (df_train['city_top'].value_counts())  
print (df_train['industry_top'].value_counts())  
print (df_train['location_grp'].value_counts())  
print (df_train['finance'].value_counts())  
print (df_train['advert'].value_counts())  
print (df_train['constr'].value_counts())  
print (df_train['health'].value_counts())  
print (df_train['NPO'].value_counts())  
print (df_train['retail'].value_counts())  
print (df_train['realest'].value_counts())  
print (df_train['manuf'].value_counts())  
print (df_train['insurance'].value_counts())  
print (df_train['market'].value_counts())  
print (df_train['tech'].value_counts())  
print (df_train['edu'].value_counts())  
print (df_train['consult'].value_counts())  
print (df_train['telco'].value_counts())  
print (df_train['AIML'].value_counts())  
print (df_train['projman'].value_counts())  
print (df_train['biotech'].value_counts())  


US    5646
CA    1135
GB     978
FR      26
IT      26
DE      17
CN       1
BR       1
CH       1
DK       1
Name: address_country_code, dtype: int64
11-50         2788
51-200        2439
201-500        878
1-10           775
501-1000       399
1001-5000      382
10001+          92
5001-10000      79
Name: company_size, dtype: int64
1     4035
2     1567
3      736
4      432
5      307
6      173
7      122
8       74
9       52
10      47
12      42
11      38
13      30
15      18
14      17
17      14
18      11
22      11
23      10
20       8
16       8
21       6
26       6
19       5
27       5
32       4
25       4
24       4
31       3
28       3
38       3
48       2
29       2
35       2
41       2
36       2
30       2
34       2
54       2
60       2
44       1
40       1
68       1
52       1
49       1
72       1
43       1
33       1
45       1
53       1
55       1
42       1
46       1
66       1
74       1
82       1
90       1
39       1
95       1
Name: location_

In [301]:
x = df_train['unique_key'].value_counts()[df_train['unique_key'].value_counts()>1]

 

In [302]:
x

QTEC Solutions_2002_US                     2
Gannett Fleming_1915_US                    2
Blackhawk Bank_1881_US                     2
Security 101_2003_US                       2
A-Gas_1993_GB                              2
Santinelli International_1973_US           2
Ampco Pumps Company_1948_US                2
TigerConnect_2010_US                       2
One Ring Networks_2010_US                  2
CareOregon_1994_US                         2
Stay-Lite Lighting_1971_US                 2
UserTesting_2007_US                        2
Evernote_2008_US                           2
ForgeRock_2010_US                          2
Calpine_1984_US                            2
Wells Enterprises_1913_US                  2
Imperva_2002_US                            2
Total Air Supply_1975_US                   2
Seven Lakes Technologies_2009_US           2
Intelligere_1979_US                        2
Avionos_2014_US                            2
GoEngineer_1984_US                         2
Tour Exper

In [167]:
y= list(x.index)

In [168]:
print (y)

['QTEC Solutions_2002_US', 'Gannett Fleming_1915_US', 'Blackhawk Bank_1881_US', 'Security 101_2003_US', 'A-Gas_1993_GB', 'Santinelli International_1973_US', 'Ampco Pumps Company_1948_US', 'TigerConnect_2010_US', 'One Ring Networks_2010_US', 'CareOregon_1994_US', 'Stay-Lite Lighting_1971_US', 'UserTesting_2007_US', 'Evernote_2008_US', 'ForgeRock_2010_US', 'Calpine_1984_US', 'Wells Enterprises_1913_US', 'Imperva_2002_US', 'Total Air Supply_1975_US', 'Seven Lakes Technologies_2009_US', 'Intelligere_1979_US', 'Avionos_2014_US', 'GoEngineer_1984_US', 'Tour Experience Golf_2016_CA', 'Ziglu_2018_GB', 'Altitude Energy Partners_2015_US', 'Codeplay Software_2002_GB', 'W.E. Cox Claims Group_1961_GB', 'Ness Digital Engineering_1998_US', 'Syntellis Performance Solutions_2020_US', 'Insureon_2011_US', 'Seaway Plastics Engineering_1974_US', 'Ziath_2005_GB', 'Univar Solutions_1924_US', 'HobbyTown_1980_US', 'WideOrbit_1999_US', 'Gerald Eve_1930_GB', 'EdgeLink_2003_US', 'Abel Noser_1975_US', 'GameAddik_2

In [176]:
#print (df_train[df_train['unique_key'] in y])
z = df_train[df_train['unique_key'].isin(y)].sort_values(by=['unique_key'])

In [177]:
print (z)

     address_country_code  employees_num company_size  location_counts  \
7279                   GB          315.0     501-1000               12   
334                    GB          315.0     501-1000               12   
7988                   US           55.0       51-200                5   
1285                   US           55.0       51-200                5   
548                    US          177.0       51-200                2   
7804                   US          177.0       51-200                2   
1113                   US           69.0       51-200                4   
5278                   US           69.0       51-200                4   
529                    US          184.0       51-200                1   
3944                   US          184.0       51-200                1   
5035                   US         4838.0   5001-10000                2   
23                     US         4838.0   5001-10000                2   
5752                   US          169

In [181]:
z[['address_country_code','employees_num','company_size','location_counts' ,'acquired','revenue' ,'website_sfx','founded_era' ,'city_top','industry_top','location_grp' ,'unique_key']]

address_country_code  employees_num company_size  location_counts  \
7279                   GB          315.0     501-1000               12   
334                    GB          315.0     501-1000               12   
7988                   US           55.0       51-200                5   
1285                   US           55.0       51-200                5   
548                    US          177.0       51-200                2   
7804                   US          177.0       51-200                2   
1113                   US           69.0       51-200                4   
5278                   US           69.0       51-200                4   
529                    US          184.0       51-200                1   
3944                   US          184.0       51-200                1   
5035                   US         4838.0   5001-10000                2   
23                     US         4838.0   5001-10000                2   
5752                   US          169.0      201-500               10   
576                    US          169.0      201-500               10   
763                    CA          122.0       51-200               10   
4116                   CA          122.0       51-200               10   
50                     US         2047.0    1001-5000                1   
4508                   US         2047.0    1001-5000                1   
150                    US          753.0     501-1000                1   
5652                   US          753.0     501-1000                1   
1050                   GB           76.0       51-200                1   
7997                   GB           76.0       51-200                1   
7183                   US           89.0        11-50                2   
936                    US           89.0        11-50                2   
5302                   US          377.0      201-500                1   
273                    US          377.0      201-500                1   
768                    CA          121.0       51-200                4   
4802                   CA          121.0       51-200                4   
3265                   US          983.0     501-1000                4   
109                    US          983.0     501-1000                4   
3807                   CA           22.0        11-50                2   
2026                   CA           22.0        11-50                2   
46                     US         2323.0    1001-5000                1   
7835                   US         2323.0    1001-5000                1   
189                    GB          599.0     501-1000                1   
6615                   GB          599.0     501-1000                1   
226                    US          487.0      201-500               12   
7952                   US          487.0      201-500               12   
7888                   US          281.0       51-200                1   
367                    US          281.0       51-200                1   
7527                   US         1676.0    1001-5000               26   
73                     US         1676.0    1001-5000               26   
725                    US          128.0       51-200                2   
3433                   US          128.0       51-200                2   
1147                   US           66.0        11-50                1   
5939                   US           66.0        11-50                1   
726                    US          128.0       51-200                1   
4044                   US          128.0       51-200                1   
20                     US         5459.0    1001-5000                1   
4084                   US         5459.0    1001-5000                1   
5585                   US           72.0       51-200                9   
1076                   US           72.0       51-200                9   
6641                   US           15.0        11-50                1   
2350     

In [191]:
df2 = df_train[~((df_train['unique_key'].isin(y)) & (df_train['acquired'] == 0))]
#df2 = df_train[(~(df_train['unique_key'].isin(y)))]


In [195]:
df2['unique_key'].value_counts()[df2['unique_key'].value_counts()>1]

Series([], Name: unique_key, dtype: int64)

In [196]:
df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7787 entries, 0 to 8091
Data columns (total 29 columns):
address_country_code    7787 non-null object
employees_num           7787 non-null float64
company_size            7787 non-null object
location_counts         7787 non-null int64
acquired                7787 non-null int64
revenue                 7787 non-null int64
website_sfx             7787 non-null object
founded_era             7787 non-null object
city_top                7787 non-null object
industry_top            7787 non-null object
location_grp            7787 non-null object
finance                 7787 non-null int64
advert                  7787 non-null int64
constr                  7787 non-null int64
health                  7787 non-null int64
NPO                     7787 non-null int64
retail                  7787 non-null int64
realest                 7787 non-null int64
manuf                   7787 non-null int64
insurance               7787 non-null int64
mark

In [218]:
print (df2['acquired'].value_counts())   

0    4695
1    3092
Name: acquired, dtype: int64


In [ ]:
# train models 

In [197]:
train_cols = ['address_country_code','employees_num','company_size','location_counts','revenue','website_sfx','founded_era','city_top','industry_top','location_grp','finance','advert','constr','health','NPO','retail','realest','manuf','insurance','market','tech','edu','consult','telco','AIML','projman','biotech']
target_col = ['acquired']
X = df2[train_cols]
y = df2[target_col]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=0)

In [198]:
print (X_train)

     address_country_code  employees_num company_size  location_counts  \
5262                   CA            7.0         1-10                1   
1206                   US           61.0       51-200                3   
4904                   US           16.0        11-50                1   
923                    US           92.0       51-200               12   
5772                   US           30.0        11-50                1   
2648                   US            9.0         1-10                1   
849                    US          105.0       51-200                1   
6966                   US          240.0      201-500                2   
8021                   US           81.0       51-200                2   
1019                   US           79.0        11-50                1   
3505                   US           47.0       51-200                2   
4717                   US          247.0      201-500               18   
7413                   US           10

In [199]:
categorical_feature_mask = X.dtypes==object
categorical_features = X.columns[categorical_feature_mask].tolist()
numeric_feature_mask = X.dtypes!=object
numeric_features = X.columns[numeric_feature_mask].tolist()

In [200]:
categorical_transformer = Pipeline(steps=[
    ('cat_imputer', SimpleImputer(strategy='most_frequent')),
    ('onehot', OneHotEncoder(handle_unknown='ignore')),])

In [201]:
numeric_transformer = Pipeline(steps=[
    ('num_imputer', SimpleImputer(strategy='mean')),
    ('scaler', StandardScaler()),])

In [202]:
preprocessor = ColumnTransformer(
    transformers=[
        ('num', numeric_transformer, numeric_features),
        ('cat', categorical_transformer, categorical_features)
    ])

In [ ]:
# TREE

In [213]:
pipeline = make_pipeline(OneHotEncoder(handle_unknown="ignore"), DecisionTreeClassifier())
hparams = {'decisiontreeclassifier__max_depth': [2,3,4], 'decisiontreeclassifier__min_samples_leaf': [3,4]}  # [3,4]}
clf = GridSearchCV(pipeline, hparams, cv=5)
clf.fit(X_train, y_train)
clf.best_params_
y_pred = clf.predict(X_test)
y_pred



array([0, 0, 1, ..., 0, 0, 0], dtype=int64)

In [214]:
# Model Performance
conf_matrix = confusion_matrix(y_true=y_test, y_pred=y_pred)
print (conf_matrix)
print('Precision: %.3f' % precision_score(y_test, y_pred, average='micro'))
print('Recall: %.3f' % recall_score(y_test, y_pred, average='micro'))
print('F1 Score: %.3f' % f1_score(y_test, y_pred, average='micro'))
print('F1 W Score: %.3f' % f1_score(y_test, y_pred, average='weighted'))

[[1112  289]
 [ 381  555]]
Precision: 0.713
Recall: 0.713
F1 Score: 0.713
F1 W Score: 0.710


## R forest

In [217]:
pipeline = Pipeline([
     ('preprocessor', preprocessor),
     ('rf', RandomForestClassifier(n_estimators=60))
])

In [216]:
pipeline = make_pipeline(preprocessor, RandomForestClassifier(n_estimators=60))
hparams = {'randomforestclassifier__max_features' : [0.7,0.75,0.8],'randomforestclassifier__max_depth': [4, 5, 6,7], 'randomforestclassifier__min_samples_leaf':[15,20,25]}

clf = GridSearchCV(pipeline, hparams, cv=6)
clf.fit(X_train, y_train.values.ravel()) 
print (clf.best_params_)
y_pred = clf.predict(X_test)
print (y_pred)

{'randomforestclassifier__max_depth': 7, 'randomforestclassifier__max_features': 0.7, 'randomforestclassifier__min_samples_leaf': 20}
[0 0 1 ... 0 0 0]


In [212]:
conf_matrix = confusion_matrix(y_true=y_test, y_pred=y_pred)
print (conf_matrix)
print('Precision: %.3f' % precision_score(y_test, y_pred, average='micro'))
print('Recall: %.3f' % recall_score(y_test, y_pred, average='micro'))
print('F1 Score: %.3f' % f1_score(y_test, y_pred, average='micro'))
print('F1 W Score: %.3f' % f1_score(y_test, y_pred, average='weighted'))

[[1104  297]
 [ 350  586]]
Precision: 0.723
Recall: 0.723
F1 Score: 0.723
F1 W Score: 0.722


In [220]:
p = clf.predict_proba(X_test)  

In [280]:
w = p[:,1]

In [284]:
test = y_test['acquired'].tolist()

In [287]:
w = list(w)


In [298]:
q = pd.DataFrame(list(zip(w, test)),
              columns=['proba','target'])


In [300]:
q.sort_values(by='proba', ascending=False)


proba  target
2299  0.867467       1
2028  0.863136       1
41    0.860523       1
1382  0.842505       1
2047  0.832518       0
903   0.831998       1
280   0.830683       1
1875  0.830188       0
1171  0.829708       1
1221  0.829655       0
101   0.829487       1
2307  0.829316       0
772   0.827719       0
574   0.827121       1
587   0.826324       1
2124  0.825741       1
358   0.825593       1
2289  0.824988       1
1806  0.824729       1
2182  0.823841       1
352   0.822717       1
941   0.822165       1
1586  0.821419       1
2175  0.821126       1
2057  0.821122       1
800   0.819939       0
1086  0.819607       1
2     0.819555       1
953   0.819441       1
1672  0.818763       1
217   0.818447       0
955   0.818330       1
1982  0.817589       1
1247  0.816814       1
1841  0.815667       1
2018  0.815662       1
2158  0.815662       1
2248  0.815613       1
608   0.815564       1
1638  0.815478       1
1999  0.815321       1
1225  0.813781       1
709   0.813327       1
1556  0.813078       1
1380  0.811884       1
340   0.811364       1
2077  0.808954       0
543   0.808948       1
2321  0.807024       1
99    0.806989       1
1417  0.806207       1
780   0.806117       1
1813  0.805944       1
153   0.805944       1
1907  0.805905       1
216   0.805680       1
520   0.805494       1
936   0.804645       1
1778  0.803963       0
1036  0.803497       1
2144  0.803326       1
327   0.803261       1
354   0.802274       1
2293  0.802024       0
398   0.801407       1
794   0.801359       0
430   0.800512       0
2042  0.800470       1
1765  0.800442       1
1661  0.800045       0
968   0.800012       1
1631  0.799034       1
2309  0.798618       1
751   0.798434       1
2139  0.798434       1
1285  0.798410       1
1724  0.797550       1
2009  0.797350       1
733   0.797103       1
957   0.795662       1
710   0.795468       1
1231  0.794817       1
2085  0.794745       1
1058  0.794720       1
875   0.794698       1
1323  0.794545       1
2185  0.794023       1
49    0.793530       1
1864  0.793051       1
985   0.792827       1
2306  0.792680       1
1828  0.792497       0
1126  0.792177       1
1905  0.791521       1
1065  0.791303       0
1261  0.790752       0
1388  0.790523       1
1457  0.790278       1
595   0.790127       0
933   0.789881       0
422   0.789837       0
1937  0.789067       1
45    0.788922       1
1370  0.788800       1
1991  0.788799       1
1551  0.788177       1
1222  0.788177       1
82    0.787949       1
1249  0.787703       1
2210  0.787665       0
979   0.787665       1
2062  0.787541       1
1502  0.787124       1
418   0.786805       1
335   0.786501       1
1329  0.786390       1
741   0.786083       1
691   0.786083       1
2230  0.785968       1
841   0.785909       1
2014  0.785390       0
699   0.785215       0
1856  0.785189       1
391   0.783876       1
2186  0.783863       1
1829  0.783620       1
934   0.783620       1
98    0.783522       1
1819  0.783324       1
930   0.782724       1
427   0.782500       1
1455  0.782419       0
1180  0.782419       1
1472  0.781443       1
2266  0.781100       1
1305  0.780480       1
1486  0.780026       1
1490  0.780020       1
250   0.779814       1
1241  0.779245       0
813   0.779164       1
1912  0.778649       1
1603  0.778276       1
718   0.778246       1
35    0.778069       1
1474  0.777945       0
133   0.777146       1
8     0.777146       1
506   0.776966       1
855   0.776895       1
965   0.776866       1
1897  0.776453       1
977   0.776360       1
1326  0.776274       1
1535  0.776235       1
1973  0.776193       1
122   0.776031       1
417   0.775892       1
1149  0.774267       1
1808  0.774202       1
322   0.773659       1
180   0.773658       1
1831  0.773398       1
458   0.773147       1
831   0.773145       1
1904  0.773123       1
1938  0.772790       0
1826  0.771475       1
1317  0.771417       1
108   0.771206       0
871   0.771136       1
235   0.770843       1
815   0.770413       1
33    0

In [ ]:


1  232	191	82.3%	0.39	2.11
2  232	158	68.1%	0.39	1.75
3  232	142	61.2%	0.39	1.57
4  232	127	54.7%	0.39	1.40
5  232	122	52.6%	0.39	1.35
6  232	84	36.2%	0.39	0.93
7  232	63	27.2%	0.39	0.70
8  232	36	15.5%	0.39	0.40
9  232	15	6.5%	0.39	0.17
10 232	2	0.9%	0.39	0.02
